## Лабораторная работа №6
### Задание 1
Провести классификацию найденного датасета, методами CatBoost . В формате Markdown написать пояснения. Объяснить почему были выбраны именно такие гиперпараметры, была ли перекрестная проверка, и т.д.
Если не установлен модуль CatBoost необходимо в консоль ввести команду pip install catboost

### Выполнение работы:
#### Шаг 1. Загрузка датасета

In [2]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from catboost import CatBoostClassifier
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import accuracy_score, classification_report
from tqdm import tqdm


df = pd.read_csv("./Base_min_shuffled.csv")

y = df["fraud_bool"]
X = df.drop("fraud_bool", axis=1)


columns_to_drop = ['payment_type', 'employment_status', 'source', 'device_os','housing_status']

# Удаление указанных столбцов
df = df.drop(columns=columns_to_drop)

y = df["fraud_bool"]
X = df.drop("fraud_bool", axis=1)

# Разделение на тренировочные и тестовые данные
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Стандартизация данных
scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)


#### Шаг 3. Метод CatBoost
CatBoost - это высокоэффективная библиотека градиентного бустинга, разработанная для эффективной работы с категориальными признаками. Она автоматически обрабатывает категориальные признаки, не требуя их предварительного кодирования. Вот некоторые гиперпараметры CatBoost и их описание:

### depth (глубина дерева):

Описание: Максимальная глубина каждого дерева в ансамбле.
Возможные значения: Любое целое положительное число.

### learning_rate (скорость обучения):

Описание: Коэффициент, определяющий величину шага градиентного спуска. Низкая скорость обучения может улучшить обобщающую способность модели.
Возможные значения: Любое положительное число.

### l2_leaf_reg (L2 регуляризация):

Описание: Сила L2-регуляризации для листьев дерева.
Возможные значения: Любое положительное число.

### iterations (количество итераций):

Описание: Количество деревьев в ансамбле (аналогично n_estimators в других моделях).
Возможные значения: Любое целое положительное число.

### loss_function (функция потерь):

Описание: Функция потерь, которая оптимизируется во время обучения.
Возможные значения: 'MultiClass' (для многоклассовой классификации) или 'Logloss' (логистическая регрессия).

In [3]:
# Определение параметров для CatBoost
param_grid_catboost = {
    'depth': [1, 4, 7, 10],
    'learning_rate': [0.01, 0.1, 1],
    'l2_leaf_reg': [1, 3, 5, 9],
    'iterations': [100, 200,],
    'depth': [0, 3, 6],
    'loss_function': ['MultiClass', 'Logloss']
}

# Создание модели CatBoost
catboost = CatBoostClassifier()

# Подбор оптимальных параметров с помощью перекрестной проверки для CatBoost
grid_search_catboost = GridSearchCV(catboost, param_grid_catboost, refit=True, verbose=3, cv=5)
grid_search_catboost.fit(X_train, y_train)

# Получение лучших параметров для CatBoost
best_params_catboost = grid_search_catboost.best_params_
best_score_catboost = grid_search_catboost.best_score_

Fitting 5 folds for each of 144 candidates, totalling 720 fits
0:	learn: 0.6888325	total: 139ms	remaining: 13.8s
1:	learn: 0.6846035	total: 141ms	remaining: 6.9s
2:	learn: 0.6804581	total: 142ms	remaining: 4.6s
3:	learn: 0.6763943	total: 144ms	remaining: 3.45s
4:	learn: 0.6724102	total: 146ms	remaining: 2.76s
5:	learn: 0.6685039	total: 147ms	remaining: 2.3s
6:	learn: 0.6646736	total: 148ms	remaining: 1.97s
7:	learn: 0.6609176	total: 150ms	remaining: 1.73s
8:	learn: 0.6572340	total: 153ms	remaining: 1.54s
9:	learn: 0.6536214	total: 154ms	remaining: 1.39s
10:	learn: 0.6500781	total: 156ms	remaining: 1.26s
11:	learn: 0.6466024	total: 158ms	remaining: 1.16s
12:	learn: 0.6431930	total: 160ms	remaining: 1.07s
13:	learn: 0.6398484	total: 161ms	remaining: 990ms
14:	learn: 0.6365671	total: 163ms	remaining: 923ms
15:	learn: 0.6333477	total: 164ms	remaining: 862ms
16:	learn: 0.6301889	total: 166ms	remaining: 809ms
17:	learn: 0.6270894	total: 167ms	remaining: 762ms
18:	learn: 0.6240479	total: 169m

## Вывод результатов


In [4]:
test_score = grid_search_catboost.score(X_test, y_test)
print("Лучшие параметры для CatBoost:", best_params_catboost)
print("Лучший результат (точность) для CatBoost:", best_score_catboost)
print("Точность на тестовом наборе данных:", test_score)

best_model = grid_search_catboost.best_estimator_
predictions = best_model.predict(X_test)

# Отчет по классификации
print("\nОтчет по классификации:")
print(classification_report(y_test, predictions))

Лучшие параметры для CatBoost: {'depth': 3, 'iterations': 200, 'l2_leaf_reg': 1, 'learning_rate': 0.1, 'loss_function': 'MultiClass'}
Лучший результат (точность) для CatBoost: 0.8670833333333334
Точность на тестовом наборе данных: 0.87375

Отчет по классификации:
              precision    recall  f1-score   support

           0       0.89      0.97      0.93      2038
           1       0.65      0.35      0.45       362

    accuracy                           0.87      2400
   macro avg       0.77      0.66      0.69      2400
weighted avg       0.86      0.87      0.86      2400

